In [2]:
KENLM_BUILD_PATH='/home/students/s434708/kenlm/build'

### Preprocessing danych

In [ ]:
import pandas as pd
import csv
import regex as re

In [ ]:
def clean_text(text):
    text = text.lower().replace('-\\n', '').replace('\\n', ' ')
    text = re.sub(r'\p{P}', '', text)

    return text

In [ ]:
train_data = pd.read_csv('train/in.tsv.xz', sep='\t', error_bad_lines=False, warn_bad_lines=False, header=None, quoting=csv.QUOTE_NONE)
train_labels = pd.read_csv('train/expected.tsv', sep='\t', error_bad_lines=False, warn_bad_lines=False, header=None, quoting=csv.QUOTE_NONE)

train_data = train_data[[6, 7]]
train_data = pd.concat([train_data, train_labels], axis=1)

train_data['text'] = train_data[6] + train_data[0] + train_data[7]
train_data = train_data[['text']]

with open('processed_train.txt', 'w') as file:
    for _, row in train_data.iterrows():
        text = clean_text(str(row['text']))
        file.write(text + '\n')

### Model kenLM

In [4]:
!$KENLM_BUILD_PATH/bin/lmplz -o 5 --skip_symbols < processed_train.txt > model.arpa

=== 1/5 Counting and sorting n-grams ===
Reading /home/students/s434708/Desktop/Modelowanie Języka/challenging-america-word-gap-prediction-kenlm/processed_train.txt
----5---10---15---20---25---30---35---40---45---50---55---60---65---70---75---80---85---90---95--100
********************************Warning: <s> appears in the input.  All instances of <s>, </s>, and <unk> will be interpreted as whitespace.
********************************************************************
Unigram tokens 135911223 types 4381594
=== 2/5 Calculating and sorting adjusted counts ===
Chain sizes: 1:52579128 2:1295655936 3:2429355008 4:3886967808 5:5668495360
Statistics:
1 4381594 D1=0.841838 D2=1.01787 D3+=1.21057
2 26800631 D1=0.836734 D2=1.01657 D3+=1.19437
3 69811700 D1=0.878562 D2=1.11227 D3+=1.27889
4 104063034 D1=0.931257 D2=1.23707 D3+=1.36664
5 119487533 D1=0.938146 D2=1.3058 D3+=1.41614
Memory estimate for binary LM:
type      MB
probing 6752 assuming -p 1.5
probing 7917 assuming -r models -p 1.5
tri

In [6]:
!$KENLM_BUILD_PATH/bin/build_binary model.arpa model.binary

Reading model.arpa
----5---10---15---20---25---30---35---40---45---50---55---60---65---70---75---80---85---90---95--100
****************************************************************************************************
/home/students/s434708/kenlm/util/file.cc:86 in int util::CreateOrThrow(const char*) threw ErrnoException because `-1 == (ret = open(name, 0100 | 01000 | 02, 0400 | 0200 | (0400 >> 3) | ((0400 >> 3) >> 3)))'.
No space left on device while creating model.binary Byte: 94
ERROR


In [7]:
!rm processed_train.txt

In [8]:
!rm model.arpa

### Predykcje

In [ ]:
import kenlm

In [ ]:
test_str = 'really good'

model = kenlm.Model('model.binary')
print(model.score(test_str, bos = True, eos = True))

In [ ]:
for i in model.full_scores(test_str):
    print(i)